# Что такое tensor parallel и с чем это едят

Есть много вариантов как уместить model, optimizer, gradients в gpu, можно держать копию model, optimizer, gradients в каждую карту, это назвывается DDP(distributed data parallel), оно хорошо и быстро работает когда у нас небольшая модель и мы можем держать копии в каждой карте. 

![ddp](https://s2.loli.net/2022/01/28/WSAensMqjwHdOlR.png)

Современные LM содержат 1B+ параметров, а Llama 7b как следует из названия - целых 7!

Соотвественно нам бы хотелось разложить модель по слоям на разные карты, а оптимайзер в каждую карту(просто чтобы экономить время на пересылку между картами), подробнее почитать про то как это работает в [статье](https://colossalai.org/docs/concepts/paradigms_of_parallelism/) 

![ds3](https://www.deepspeed.ai/assets/images/zero3-offload-memory-overview.png)

Вообще картинка выше из статьи про ZERO- технологии microsoft для распределенного обучения, почитать [тут](https://www.deepspeed.ai/2021/03/07/zero3-offload.html)

In [11]:
!nvidia-smi

Fri Jun 23 14:33:02 2023       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.161.03   Driver Version: 470.161.03   CUDA Version: 11.4     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla T4            Off  | 00000000:00:04.0 Off |                    0 |
| N/A   41C    P8     9W /  70W |      3MiB / 15109MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
|   1  Tesla T4            Off  | 00000000:00:05.0 Off |                    0 |
| N/A   

# Установим все что нам нужно

In [7]:
%%capture
!pip install git+https://github.com/huggingface/transformers.git@main
!pip install git+https://github.com/huggingface/accelerate@main
!pip install tensor_parallel
!pip install bitsandbytes
!pip install peft 
!pip install wandb

In [12]:
import torch
import re
from multiprocessing import Pool
import wandb
from transformers import GPT2TokenizerFast, GPT2LMHeadModel
from torch.utils.data import DataLoader
from datasets import load_dataset
from torch.utils.data import Dataset
from tqdm import tqdm
from transformers import  AdamW, get_linear_schedule_with_warmup
from torch import optim
SEED = 27

torch.manual_seed(SEED)
torch.cuda.manual_seed(SEED)

In [13]:
def print_trainable_parameters(model):
    """
    Prints the number of trainable parameters in the model.
    """
    trainable_params = 0
    all_param = 0
    for _, param in model.named_parameters():
        all_param += param.numel()
        if param.requires_grad:
            trainable_params += param.numel()
    print(
        f"trainable params: {trainable_params} || all params: {all_param} || trainable%: {100 * trainable_params / all_param}"
    )

In [14]:
MODEL_NAME = "huggyllama/llama-7b"# берем именно ее, у нее правильно выставлены BOS, EOS токены

In [15]:
import transformers
import accelerate
from transformers.utils.bitsandbytes import replace_with_bnb_linear
import tensor_parallel as tp

tokenizer = transformers.LlamaTokenizer.from_pretrained(MODEL_NAME)
special_tokens_dict = {'additional_special_tokens': ['user:', 'bot:']}
tokenizer.add_special_tokens({'eos_token': '<instructionE>'})
tokenizer.add_special_tokens({'bos_token': '<instructionE>'})
tokenizer.add_special_tokens({'pad_token': '[PAD]'})

tokenizer.add_special_tokens(special_tokens_dict)


model = transformers.AutoModelForCausalLM.from_pretrained(MODEL_NAME,  torch_dtype=torch.float16, low_cpu_mem_usage=True)
model.resize_token_embeddings(len(tokenizer))

model = tp.TensorParallelPreTrainedModel( # литерали одной строкой кладем модель на две карты, все, изи пизи лемон сквизи и никаких deepspeed конфигов 
        model,
        device_ids=["cuda:0", "cuda:1"],)
    
#model = replace_with_bnb_linear(model, quantization_config=transformers.utils.quantization_config.BitsAndBytesConfig(load_in_8bit=True))
#model.is_loaded_in_8bit = True


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /opt/conda/lib/python3.10/site-packages/bitsandbytes/libbitsandbytes_cuda117.so
CUDA SETUP: CUDA runtime path found: /opt/conda/lib/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 7.5
CUDA SETUP: Detected CUDA version 117
CUDA SETUP: Loading binary /opt/conda/lib/python3.10/site-packages/bitsandbytes/libbitsandbytes_cuda117.so...


/opt/conda/lib/python3.10/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/usr/local/cuda/lib'), PosixPath('/usr/local/lib/x86_64-linux-gnu'), PosixPath('/usr/local/nvidia/lib')}
  warn(msg)


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [16]:
model # модель обернута в TP класс, не все hf методы переопределены, например  model.resize_token_embeddings лучше делать пока модель лежит в CPU и обычный hf class

TensorParallelPreTrainedModel(
  (wrapped_model): TensorParallel(
    (module_shards): ModuleList(
      (0-1): 2 x LlamaForCausalLM(
        (model): LlamaModel(
          (embed_tokens): TensorParallelWrapper(
            (tp_wrapped_module): Embedding(32004, 4096)
          )
          (layers): ModuleList(
            (0-31): 32 x LlamaDecoderLayer(
              (self_attn): TensorParallelWrapper(
                (tp_wrapped_module): LlamaAttention(
                  (q_proj): Linear(in_features=4096, out_features=2048, bias=False)
                  (k_proj): Linear(in_features=4096, out_features=2048, bias=False)
                  (v_proj): Linear(in_features=4096, out_features=2048, bias=False)
                  (o_proj): Linear(in_features=2048, out_features=4096, bias=False)
                  (rotary_emb): LlamaRotaryEmbedding()
                )
              )
              (mlp): TensorParallelWrapper(
                (tp_wrapped_module): LlamaMLP(
                  (gate_p

# Датасет
В качестве датасета я использовала матрешку - синтетический датасет диалогов на подобии SODA, он собран из Gpt3.5 Api

In [17]:
from datasets import load_dataset

dataset = load_dataset("zjkarina/matreshka")

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Dataset parquet downloaded and prepared to /root/.cache/huggingface/datasets/parquet/zjkarina--matreshka-47186eb123d38b60/0.0.0/0b6d5799bb726b24ad7fc7be720c170d8e497f575d02d47537de9a5bac074901. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

In [18]:
print(dataset['train'][0]['role'], dataset['train'][0]['dialog'], dataset['train'][0]['persona'], dataset['train'][0]['summary'] )

['user', 'bot', 'user'] ['Какое место в мире ты хочешь посетить?', 'Я мечтаю о поездке в Японию. А ты?', 'Мне всегда хотелось посетить Италию, особенно Рим.'] Первый собеседник интересуется тем, какое место в мире хочет посетить его собеседник. Первый собеседник спрашивает собеседника о его мечте посетить место в мире и отвечает, что мечтает посетить Японию. Второй собеседник выражает желание посетить Италию, особенно Рим.


In [19]:
tokenizer.max_model_input_sizes

{'hf-internal-testing/llama-tokenizer': 2048}

In [20]:
class DialogDataset(Dataset):
    def __init__(self, tokenizer, dataset_chat):
        self.tokenized = []
        dataset_my_train = dataset_chat['train']
        dataset_my_val = dataset_chat['validation']
    
        for dia in tqdm(dataset_my_train):
            dialog = ""
            try:
                for idx, sen in enumerate(zip(dia['role'], dia['dialog'])):
                    if sen[0] == 'user' and idx != 0:
                        sen = (f" <instructionE> user", sen[1])
                        dialog += ': '.join(sen)
                    elif sen[0] == 'user' and idx == 0:
                        sen = (f"user", sen[1])
                        dialog += ': '.join(sen)
                    else:
                        sen = (f" bot", sen[1])
                        dialog += ': <instructionE> '.join(sen)
                enc = self._encode(text=dialog, tokenizer=tokenizer)
                self.tokenized += [enc]
            except:
                pass
        for dia in tqdm(dataset_my_val):
            dialog = ""
            try:
                for idx, sen in enumerate(zip(dia['role'], dia['dialog'])):
                    if sen[0] == 'user' and idx != 0:
                        sen = (f" <instructionE> user", sen[1])
                        dialog += ': '.join(sen)
                    elif sen[0] == 'user' and idx == 0:
                        sen = (f"user", sen[1])
                        dialog += ': '.join(sen)
                    else:
                        sen = (f" bot", sen[1])
                        dialog += ': <instructionE> '.join(sen)
                enc = self._encode(text=dialog, tokenizer=tokenizer)
                self.tokenized += [enc]
            except:
                pass

    def __len__(self):
        return len(self.tokenized)

    def __getitem__(self, item):
        return self.tokenized[item] 

    @staticmethod
    def _encode(text, tokenizer):
        encoded_sample = tokenizer(text, padding='max_length', max_length=256,  truncation=True, return_tensors='pt')

        return encoded_sample

In [21]:
data = DialogDataset(tokenizer=tokenizer, dataset_chat=dataset)
train_dataloader = DataLoader(
        data, batch_size=1, shuffle=True)

100%|██████████| 1664/1664 [00:02<00:00, 686.40it/s]


In [22]:
tokenizer.decode(data.tokenized[10]['input_ids'][0])

'<instructionE> user: Привет, когда ты родился? bot: <instructionE> Я родился в 1990 году. <instructionE> user: В каком городе ты живешь? bot: <instructionE> Я живу в Москве. <instructionE> user: Интересно, а ты любишь смотреть фильмы? [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [PAD] [P

# Обернем нашу модель в Lora адаптер

![lora](https://docs.adapterhub.ml/_images/architecture.png) 
 Если коротко, то Lora адаптер это способ обучать <1% параметров модели при этом получать сопостовимые по метрикам результаты, мы обучаем специальные адаптеры, они расположены в r=16 то LORA расставиться после linear в матричку в 16 раз меньше чем оригинальная, а сама llama при этом будет заморожена

почитать больше про LORA можно [тут](https://docs.adapterhub.ml/methods.html) 


In [23]:
from peft import LoraConfig, get_peft_model

lora_config = LoraConfig(
    r=16, lora_alpha=32, lora_dropout=0.05, bias="none"
)
model = get_peft_model(model, lora_config)

In [24]:
print_trainable_parameters(model)

trainable params: 12582912 || all params: 6751297536 || trainable%: 0.18637768418447023


In [25]:
import wandb
api_key = 'e461a6a3bca9f7cec3390a40dc10cdf576ce3252'
wandb.login(key=api_key)

wandb: W&B API key is configured. Use `wandb login --relogin` to force relogin
wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [26]:
wandb.init(project='LLama',name='kaggle_lora')

wandb: Currently logged in as: alexwortega. Use `wandb login --relogin` to force relogin


In [27]:
from transformers import  AdamW, get_linear_schedule_with_warmup, get_cosine_schedule_with_warmup
from tqdm import tqdm
lr = 2e-5

optimizer = AdamW(model.parameters(), lr=lr, betas=(0.9, 0.999))

max_steps = 1000
if max_steps:
    total_steps = max_steps #чтобы вы не ждали миллион лет
else:
    total_steps =  len(train_dataloader)
    


scheduler = torch.optim.lr_scheduler.OneCycleLR(optimizer, max_lr=lr, total_steps=total_steps, div_factor=25, pct_start=0.2)


/opt/conda/lib/python3.10/site-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


In [28]:

import gc
counter = 0
epohs=1
for epoch in tqdm(range(epohs)):
    for input_ids in tqdm(train_dataloader):

        if counter>max_steps:
            break
            print('Finish!')


        input_ids = input_ids['input_ids'][0].to(model.device)
        optimizer.zero_grad()
        loss = model(input_ids=input_ids, labels=input_ids).loss
        #losses.append(float(loss))

        loss.backward()
        optimizer.step()

        wandb.log({'loss': loss.item()})

        del loss, input_ids
        torch.cuda.empty_cache()
        gc.collect()
        counter+=1
    

100%|██████████| 1/1 [14:28<00:00, 868.86s/it]


# 

# Ура, спустя пару часов мы доучили модель, давайте смержим LORA в модель, и загрузим ее на huggingface

In [ ]:
model = model.merge_and_unload()

In [ ]:
from huggingface_hub import notebook_login

notebook_login()

In [ ]:
with tp.save_tensor_parallel(model):
    
    # аккуратно снимаем с карт и кладем локально
    model.save_pretrained("Matreshka_Llama")

In [ ]:
model.push_to_hub("Matreshka_Llama")

## пробуем что то генерировать, обратите внимание что вам нужно поучить на всем сете, а не на первых 1000 сэмплах

In [ ]:
  gen_kwargs = {
        "min_length": 20,
        "max_new_tokens": 100,
        "top_k": 50,
        "top_p": 0.7,
        "do_sample": True,  
        "early_stopping": True,
        "no_repeat_ngram_size": 2,
        "eos_token_id": tokenizer.eos_token_id,
        "pad_token_id": tokenizer.eos_token_id,
        "use_cache": True,
        "repetition_penalty": 1.5,  
        "length_penalty": 1.2,  
        #"num_beams": 1,
        "num_return_sequences": 1
    }
inp = tokenizer.encode('<instructionE> user: Привет, когда ты родился? bot: <instructionE> ',return_tensors='pt')

In [ ]:
gen = model.generate(inp.to(model.device),**gen_kwargs)

In [ ]:
tokenizer.batch_decode(gen)# need more iters